In [10]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib as mpl
import astropy
from astropy.io import fits
from astropy.table import Table
import richardsplot
import sklearn
from sklearn.preprocessing import scale
%matplotlib inline

import bokeh.palettes as pal
from bokeh.plotting import figure, ColumnDataSource, output_file, show, output_notebook
from bokeh.models import HoverTool
from bokeh.models.annotations import Title

In [11]:
infile = 'SDSSRMMedianCIVParams_wCIVDist.csv' #load in RM CIV data
df = pd.read_csv(infile)

infile2 = 'SpringFinalFigs_moreParams.csv'
df2 = pd.read_csv(infile2)

infile3 = 'AllVLACIVParams.csv' #updated CIV data for VLA objects
df3 = pd.read_csv(infile3)

In [12]:
#Parameters to test
uniform = df2[['UNI_FLAG']].values
Miz2 = df2[['MI_Z2']].values
det = df2[['detection']].values + df2[['FIRST']].values
peak_flux = df2[['peak_flux']].values
int_flux = df2[['int_flux']].values
logL_rad = df2[['L_rad']].values
aro = df2[['alpha_ro']].values
ew_civ = df2[['EW_CIV_2']].values
voff_civ = df2[['VOFF_CIV_PEAK_2']].values
log_bh = df2[['LOGBH']].values
logedd_ratio = df2[['LOGEDD_RATIO']].values
logL_bol = df2[['LOGLBOL']].values
logL_civ = df2[['LOGL_CIV']].values
fwhm_civ = df2[['FWHM_CIV']].values


duni = (det>0)&(uniform>0) #eqw mask handles bad indexing below since we're
nduni = (det<0)&(uniform>0)#missing 2 of our targets in the new CIV analysis
dnuni = (det>0)&(uniform==0)
ndnuni = (det<0)&(uniform==0)

In [22]:
polyfit = np.load('RM_CIV_bestFitLine_noScale.npy')

scalefit = np.load('RM_CIV_bestFitLine_scale.npy')
rm_scalecoords = np.load('RM_CIVParams_scale.npy')
vla_scalecoords = np.load('VLA_CIVParams_scale.npy')

vla_proj = np.load('VLA_CIV_fitXYCoords_noScale.npy')

In [23]:
rm_blueshift = df[['Median_CIV_Blueshift']].values.reshape(133)
rm_eqw = df[['Median_CIV_EQW']].values.reshape(133)

vla_blueshift = df3[['CIV_Blueshift (km/s)']].values.reshape(50)
vla_eqw = df3[['CIV_EQW']].values.reshape(50)

-------

### Bokeh Stuff

In [24]:
def make_sameName(i): #remove necessary characters to match image formatting (only to arcsec, remove SDSS) -- elim J as well : 8/23
    
    i = list(i)
    i.pop(0)
    i.pop(0)
    i.pop(0)
    i.pop(0)
    i.pop(0)
    i.pop(4)
    i.pop(4)
    i.pop(4)
    i.pop(4)
    i.pop(4)
    i.pop(9)
    i.pop(9)
    i.pop(9)
    i.pop(9)

    i = ''.join(i)

    return i

In [25]:
sdss_names = df2[['name']].values.reshape(50)  #make array for all data of detections
image_names = [make_sameName(x) for x in sdss_names] #create list with new names titled JXXXX+XXXX

colors = ['#d51968', '#2569b4', '#ff8c00']
vla_colors = []
for i in range(len(sdss_names)):
    vla_colors.append(colors[int(det[i,0])])

vla_source = ColumnDataSource(data=dict(  #create source for detections
    
    x = vla_proj[:,0], 
    y = vla_proj[:,1], 
    sdss_name = image_names,
    imgs_4p5am = [('bokeh_imgs/4p5am/' + name + '_4p5am.png') for name in image_names], 
    imgs_90as = [('bokeh_imgs/90as/' + name + '_90as.png') for name in image_names],
    pf = peak_flux,
    intf = int_flux,
    fill = uniform,
    color = vla_colors

))

In [26]:
#output_file('interactive_VLA2018b.html')

hover = HoverTool(names = ["VLA"], tooltips='''
    <div>
        <div>
            <img
                src="@imgs_4p5am" height="250" alt="@imgs_4p5am" width="250"
                style="float: left; margin: 0px 15px 15px 0px;"
                border="2"
            ></img>
            
            <img       
                src="@imgs_90as" height="250" alt="@imgs_90as" width="250"
                style="float: left; margin: 0px 15px 15px 0px;"
                border="2"
            ></img>
        </div> 
          
        <div>
            <span style="font-size: 17px; font-weight: bold;">SDSSJ@sdss_name</span>
        </div>
        <div>
            <span style="font-size: 17px; color: #966;">Peak Flux = [@pfµJy/beam]</span>
            <span style="font-size: 17px; color: #966;">Int. Flux = [@intfµJy]</span>
        </div>
        <div>
            <span style="font-size: 17px;">CIV (Blueshift, EQW):</span>
            <span style="font-size: 15px; color: #696;">($x, $y)</span>
        </div>
    </div>


                      ''')

In [33]:
output_file('interactive_VLA2018b_RadioCIVRM_unscaled.html')
output_notebook()

p = figure(plot_width=900, plot_height=900, title="",
           x_range=[-650, 5800], y_range = [5, 360], tools=[hover, 'pan,box_zoom,wheel_zoom,save,reset,help'])


#plot background sources (cmap inverted to match original)

p.line(polyfit[:,0], polyfit[:,1], line_width = 2, color = '#1f77b4', alpha=0.4,
         legend = 'RM Fit') #FIRST sources


p.circle(x=rm_blueshift, y=rm_eqw, size = 10, color = '#1f77b4', alpha=0.2, legend = "RM")
p.circle(x=vla_blueshift, y=vla_eqw, size = 10, color = 'green', alpha=0.5, legend = "VLA")
                

p.circle(x='x', y='y', color = 'color', fill_alpha = 'fill', size = 10, alpha=0.8,
                source=vla_source, name = "VLA", legend="VLA")


p.legend.location = 'top_right'
p.legend.click_policy= 'hide'
p.legend.border_line_color = 'navy'
p.legend.border_line_alpha = 0.5
p.legend.background_fill_alpha = 0.5

p.xaxis.axis_label = 'Blueshift (km/s)'
p.yaxis.axis_label = 'EQW'
p.title.text = 'EV1 Distribution of 50 VLA Targets in Unscaled CIV Space'

show(p)

Loading BokehJS ...